In [28]:
import re
from datetime import datetime as dt

import os
import numpy as np
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point

from cartoframes.auth import set_default_credentials
from cartoframes.viz import Map, Layer, animation_widget, animation_style, basemaps

set_default_credentials('cartoframes')

In [11]:
def get_file_regex(prefix, file_datetime = None, suffix = None, ext = "csv"):
    if file_datetime is None:
        year_re = r"\d{4}"
        month_re = r"[a-zA-Z]{3}"
        day_re = r"\d{2}"
        hr_re = r"\d{2}"
        min_re = r"\d{2}"
        sec_re = r"\d{2}"
    else:
        date_string = file_datetime.strftime("%Y.%b.%d.%H.%M.%S")
        year_re, month_re, day_re, hr_re, min_re, sec_re = date_string.split(".")

    if suffix is None:
        suffix_re = r""
    else:
        suffix_re = r"\." + suffix

    file_re = re.compile(prefix+   r"\.("+ year_re + 
                                        r")\.(" + month_re + 
                                        r")\.(" + day_re    + 
                                        r")\.(" + hr_re +
                                        r")_(" + min_re + 
                                        r")_(" + sec_re + 
                                        r")" +suffix_re + 
                                        r"\." + ext + 
                                        r"")
    return file_re

def most_recent_directory_file(directory, file_regex):
    files = os.listdir(directory)
    filtered_files = [f for f in files if file_regex.search(f) is not None]
    filtered_files.sort(key = lambda x: dt_from_file_name(x, file_regex), reverse=True)
    return filtered_files[0]

def dt_from_file_name(file_name, regex):
    s = regex.search(file_name)
    file_dt = dt.strptime(''.join(s.groups()), "%Y%b%d%H%M%S")
    return file_dt

In [37]:
data_dir = "..\\output\\batch\\model_run_data\\"

project_crs = {'init': 'epsg:27700'}

file_re = get_file_regex("pedestrian_locations")
ped_locations_file = most_recent_directory_file(data_dir, file_re)

df_ped_loc = pd.read_csv(os.path.join(data_dir, ped_locations_file))

# Now split df into one for locations, one for route coords
lo_cols = [i for i in df_ped_loc.columns if 'Loc' in i]

df_loc = df_ped_loc.dropna(subset = lo_cols)
for c in lo_cols:
    df_loc[c] = df_loc[c].map(float)


gdf_loc = gpd.GeoDataFrame(df_loc, geometry=gpd.points_from_xy(df_loc.LocXString, df_loc.LocYString))
gdf_loc.crs = project_crs

gdf_loc = gdf_loc.to_crs("EPSG:4326")

In [38]:
gdf_loc.head()

ID     LocXString     LocYString  tick  run                   geometry
0   1  530511.403564  180908.766097   1.0    1  POINT (-0.12065 51.51204)
1   2  530418.088626  180819.931419   1.0    1  POINT (-0.12203 51.51126)
2   1  530511.625498  180908.573611   2.0    1  POINT (-0.12065 51.51204)
3   2  530418.386438  180820.210279   2.0    1  POINT (-0.12203 51.51127)
4   1  530511.829811  180908.362514   3.0    1  POINT (-0.12065 51.51204)

In [39]:
# Creat map for single trajectory
path_1_1 = gdf_loc.loc[(gdf_loc['run'] == 1) & (gdf_loc['ID']==1)]

Map(
        Layer(path_1_1),
        basemap=basemaps.voyager
)

In [33]:
path_1_1.crs

'EPSG:4326'

In [14]:
# Create animated map with the pedestrian locations

In [76]:
# Filter the data
gdf_run = gdf_loc[(gdf_loc['run']==2)]
n_ticks = max(gdf_run_1['tick'])

In [77]:

# Create new data source
pedestrian_paths = Source(gdf_run, credentials=None, geom_col='geometry', encode_data=False)

Map(
Layer(pedestrian_paths, 
      animation_style(
              'tick',
              duration=n_ticks/20,
              fade_in=0, 
              fade_out=0.5, 
              color=None,
              size=5, 
              opacity=None, 
              stroke_color=None, 
              stroke_width=None), 
      widgets=[
        animation_widget(
            title='Simulated Pedestrian Paths',
            description= 'Play, pause, or select the behavioural scenario'
        )],
      encode_data=False),
basemap=basemaps.voyager
)



In [52]:
gdf_run_1.head()

ID     LocXString     LocYString  tick  run                   geometry
0   1  530511.403564  180908.766097   1.0    1  POINT (-0.12065 51.51204)
1   2  530418.088626  180819.931419   1.0    1  POINT (-0.12203 51.51126)
2   1  530511.625498  180908.573611   2.0    1  POINT (-0.12065 51.51204)
3   2  530418.386438  180820.210279   2.0    1  POINT (-0.12203 51.51127)
4   1  530511.829811  180908.362514   3.0    1  POINT (-0.12065 51.51204)

In [55]:
max(pedestrian_paths['tick'])

TypeError: 'Source' object is not subscriptable

In [60]:
n_ticks

330.0